In [ ]:
'''
Script to join/merge organisations between years in OSCAR
  
This now uses the full matching across all years
  
'''

In [1]:
import pandas as pd
import numpy as np

from __future__ import unicode_literals
import unittest
import re
import sys
import pycodestyle

import math

In [4]:
baseline_oscar = pd.read_pickle('2022_11_22_matched_oscar_21_22.pkl')

# simplifies the data to a list of organisations and organisation codes (used within OSCAR)
baseline_oscar_orgs_df = organisation_code_extraction(baseline_oscar)

In [13]:
file_names = ['2015_OSCAR_Extract_2010_11.txt',
              '2015_OSCAR_Extract_2011_12.txt',
              '2015_OSCAR_Extract_2012_13.txt',
              '2015_OSCAR_Extract_2013_14.txt',
              '2015_OSCAR_Extract_2014_15.txt',
              '2017 OSCAR Extract 2015-16.csv',
              '2017 OSCAR Extract 2016-17.csv',
              '2022_OSCAR_Extract_2017_18.txt',
              '2022_OSCAR_Extract_2018_19.txt',
              '2022_OSCAR_Extract_2019_20.txt',
              '2022_OSCAR_Extract_2020_21.txt',
              '2022_OSCAR_Extract_2021_22.txt']

In [20]:
for j in range(0, len(file_names)):
    
    file_location = 'Source files\\' + file_names[j]
    
    new_oscar = pd.read_csv(file_location, delimiter='|', encoding='cp1252')
    
    # bring organisations and codes out into a unique dataframe
    new_oscar_orgs_df = organisation_code_extraction(new_oscar)
    
    # compare organisations from this year to current year and add checking information
    checked_new_oscar_orgs_df, unfound_orgs_df = checking_organisations(new_oscar_orgs_df, baseline_oscar, file_names[j])
    
    # want to group organisation information over the months into a single data line
    all_oscar_df, summary_totals_df = grouping_by_organisation(new_oscar, checked_new_oscar_orgs_df)
    
    # add year information into these dataframes
    all_oscar_df['Financial_Year'] = file_names[j][-11:-4]
    summary_totals_df['Financial_year'] = file_names[j][-11:-4]

    # save up the findings
    all_oscar_df.to_pickle(file_names[j][:-4]+'_matched.pkl')
    summary_totals_df.to_pickle(file_names[j][:-4]+'_summary_L0.pkl')

    # clean and group the oscar data
    cleaned_grouped_df = clean_group_oscar_lite(all_oscar_df)
    
    # assemble the information into a single place...
    if j == 0:
        all_values = cleaned_grouped_df
        positive_values = cleaned_grouped_df[cleaned_grouped_df['AMOUNT']>0]
        all_unfound_orgs_df = unfound_orgs_df 
    else:
        all_values = pd.concat([all_values, cleaned_grouped_df], ignore_index=True)
        positive_values = pd.concat([positive_values, cleaned_grouped_df[cleaned_grouped_df['AMOUNT']>0]], ignore_index=True)
        all_unfound_orgs_df = pd.concat([all_unfound_orgs_df, unfound_orgs_df], ignore_index=True)
        
    with pd.ExcelWriter('oscar_2021_22_test_rerun.xlsx') as writer:

        all_values.to_excel(writer, sheet_name='all_values')
#        positive_values.to_excel(writer, sheet_name='positive_values')
        all_unfound_orgs_df.to_excel(writer, sheet_name='unfound')

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\2506921955.py:5: DtypeWarning: Columns (23,24,38,87) have mixed types. Specify dtype option on import or set low_memory=False.
  new_oscar = pd.read_csv(file_location, delimiter='|', encoding='cp1252')


['more than one org code found for Children and Family Court Advisory and Support Service: CFA022'
 'more than one org code found for Children and Family Court Advisory and Support Service: CAF047']
['more than one org code found for National Employment Savings Trust: NST032'
 'more than one org code found for National Employment Savings Trust: NEM032']
['more than one org code found for Ordnance Survey: ORD084'
 'more than one org code found for Ordnance Survey: ORD085']
Student Loans Company not found in 2015_OSCAR_Extract_2010_11.txt
Legal Aid Fund: Civil not found in 2015_OSCAR_Extract_2010_11.txt
Legal Services Commission not found in 2015_OSCAR_Extract_2010_11.txt
Criminal Injuries Compensation Authority not found in 2015_OSCAR_Extract_2010_11.txt
British Educational Communications and Technology Agency not found in 2015_OSCAR_Extract_2010_11.txt
Department of Energy and Climate Change not found in 2015_OSCAR_Extract_2010_11.txt
Children and Family Court Advisory and Support Serv

Olympic Lottery Distributor not found in 2015_OSCAR_Extract_2010_11.txt
Countryside Council for Wales not found in 2015_OSCAR_Extract_2010_11.txt
Scottish Screen Lottery not found in 2015_OSCAR_Extract_2010_11.txt
Partnerships for Schools not found in 2015_OSCAR_Extract_2010_11.txt
Forensic Science Service not found in 2015_OSCAR_Extract_2010_11.txt
Channel Four Television Corporation not found in 2015_OSCAR_Extract_2010_11.txt
Civil Aviation Authority not found in 2015_OSCAR_Extract_2010_11.txt
Horserace Totalisator Board not found in 2015_OSCAR_Extract_2010_11.txt
Driving Standards Agency not found in 2015_OSCAR_Extract_2010_11.txt
NHS Estates not found in 2015_OSCAR_Extract_2010_11.txt
Medicines and Healthcare Products Regulatory Agency not found in 2015_OSCAR_Extract_2010_11.txt
Vehicle and Operator Services Agency not found in 2015_OSCAR_Extract_2010_11.txt
Commonwealth Development Corporation not found in 2015_OSCAR_Extract_2010_11.txt


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

...

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_10708\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

KeyboardInterrupt: 

In [26]:
all_oscar_df.columns

Index(['YEAR_NO', 'YEAR_SHORT_NAME', 'QUARTER_SHORT_NAME', 'MONTH_SHORT_NAME',
       'BUDGETING_ORGANISATIONS_CODE', 'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_CODE',
       'ORGANISATION_TYPE_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE',
       'ORGANISATION_TYPE_L1_LONG_NAME', 'PESA_GROUP_CODE',
       'PESA_GROUP_LONG_NAME', 'SR_GROUP_CODE', 'SR_GROUP_LONG_NAME',
       'BX_VALIDATION_GROUP_CODE', 'BX_VALIDATION_GROUP_LONG_NAME',
       'FO_VALIDATION_GROUP_CODE', 'FO_VALIDATION_GROUP_LONG_NAME',
       'ACCOUNTING_ARRANGEMENTS_CODE', 'ACCOUNTING_ARRANGEMENTS_LONG_NAME',
       'COUNTER_ORGANISATION_CODE', 'COUNTER_ORGANISATION_LONG_NAME',
       'SEGMENT_L4_CODE', 'SEGMENT_L4_LONG_NAME', 'COFOG_L0_CODE',
       'COFOG_L0_LONG_NAME', 'COFOG_L1_CODE', 'COFOG_L1_LONG_NAME',
       'COFOG_L2_CODE', 'COFOG_L2_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME',
       'CONTROL_BUDGET_L1_LONG_NAME', 'COVERAGE_L

In [18]:
for j in range(0, len(file_names)):
    
    file_location = 'Source files\\' + file_names[j]

    # read the pickle file...
    all_oscar_df = pd.read_pickle(file_names[j][:-4]+'_matched.pkl')

    # rerun the matching for each year
    # bring organisations and codes out into a unique dataframe
    new_oscar_orgs_df = organisation_code_extraction(all_oscar_df)
    
    # compare organisations from this year to current year and add checking information
    checked_new_oscar_orgs_df = checking_organisations_no_unfound(new_oscar_orgs_df, baseline_oscar, file_names[j])
    
    # want to group organisation information over the months into a single data line
    all_oscar_df, summary_totals_df = grouping_by_organisation(all_oscar_df, checked_new_oscar_orgs_df)
    
    # add year information into these dataframes
    all_oscar_df['Financial_Year'] = file_names[j][-11:-4]
    summary_totals_df['Financial_year'] = file_names[j][-11:-4]
    
    # clean and group the oscar data
    cleaned_grouped_df = clean_group_oscar_lite(all_oscar_df)
    
    # assemble the information into a single place...
    if j == 0:
        all_values = cleaned_grouped_df
        positive_values = cleaned_grouped_df[cleaned_grouped_df['AMOUNT']>0]
    else:
        all_values = pd.concat([all_values, cleaned_grouped_df], ignore_index=True)
        positive_values = pd.concat([positive_values, cleaned_grouped_df[cleaned_grouped_df['AMOUNT']>0]], ignore_index=True)
        
    with pd.ExcelWriter('oscar_2021_22_release_summarised_5.xlsx') as writer:

        all_values.to_excel(writer, sheet_name='all_values')
        positive_values.to_excel(writer, sheet_name='positive_values')
        

['more than one org code found for Children and Family Court Advisory and Support Service: CFA022'
 'more than one org code found for Children and Family Court Advisory and Support Service: CAF047']
['more than one org code found for National Employment Savings Trust: NST032'
 'more than one org code found for National Employment Savings Trust: NEM032']
['more than one org code found for Ordnance Survey: ORD084'
 'more than one org code found for Ordnance Survey: ORD085']


C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Status'] = ifg_org_stat
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Status'] = ifg_org_stat
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using

...

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['Checked_Organisation_Name'] = chk_org_name
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oscar_segment['IfG_Organisation_Type'] = ifg_org_type
C:\Users\shepleyp\AppData\Local\Temp\ipykernel_23596\332388984.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usi

In [ ]:
# this is to run against the updated organisation mapping done by Nat (and will do change in status over time)

for j in range(0, len(file_names)):
    
    # find the files
    file_location = 'Source files\\' + file_names[j]

    # read the pickle file...
    all_oscar_df = pd.read_pickle(file_names[j][:-4]+'_matched.pkl')

    # consider and update the IfG organisation information
    all_oscar_df = additional_organisation_matching(all_oscar_df, file_names[j][:-4])
    
    # clean and group the oscar data
    cleaned_grouped_df = clean_group_oscar_lite(all_oscar_df)
    
    # assemble the information into a single place...
    if j == 0:
        all_values = cleaned_grouped_df
        positive_values = cleaned_grouped_df[cleaned_grouped_df['AMOUNT']>0]
    else:
        all_values = pd.concat([all_values, cleaned_grouped_df], ignore_index=True)
        positive_values = pd.concat([positive_values, cleaned_grouped_df[cleaned_grouped_df['AMOUNT']>0]], ignore_index=True)
        
    with pd.ExcelWriter('oscar_2021_22_release_summarised_5.xlsx') as writer:

        all_values.to_excel(writer, sheet_name='all_values')
        positive_values.to_excel(writer, sheet_name='positive_values')

In [14]:
def additional_organisation_matching(all_oscar_df, file_names):
    
    # load in the additional checking
    additional_organisations = pd.read_excel('oscar_organisation_matching_unfound.xlsx')
    
    org_type = []
    org_status = []
    
    # pull organisation and match by long name
    for j in range(0, len(all_oscar_df)):
        
        new_match_info = additional_organisations[additional_organisations['ORGANISATION_LONG_NAME'] == all_oscar_df['ORGANISATION_LONG_NAME'][j]]
    
        org_type.append(new_match_info['Type_of_organisation'])
        org_status.append(new_match_info['Exact status'])
        
    all_oscar_df['Type_of_organisation'] = org_type
    all_oscar_df['Exact status'] = org_status
    
    # save the resulting file
    oscar_df.to_pickle(file_name+'_matched_over_time.pkl')
    
    return all_oscar_df

In [15]:
# build information into the new oscar dataset
def organisation_matching(org_code, org_long_name, checked_orgs_df, oscar_segment):

    chk_org_name = checked_orgs_df[checked_orgs_df['ORGANISATION_CODE']==org_code]['Checked_Organisation_Name'].values[0]
    ifg_org_type = checked_orgs_df[checked_orgs_df['ORGANISATION_CODE']==org_code]['IfG_Organisation_Type'].values[0]
    ifg_org_stat = checked_orgs_df[checked_orgs_df['ORGANISATION_CODE']==org_code]['IfG_Organisation_Status'].values[0]

    # add these to the OSCAR dataframe
    oscar_segment['Checked_Organisation_Name'] = chk_org_name
    oscar_segment['IfG_Organisation_Type'] = ifg_org_type
    oscar_segment['IfG_Organisation_Status'] = ifg_org_stat
    
    return oscar_segment

def summarise_org_spending(org_code, org_long_name, oscar_segment):
    
    # pull out the categories on the CONTROL_BUDGET_L0_LONG_NAME
    categories = oscar_segment.groupby('CONTROL_BUDGET_L0_LONG_NAME')['AMOUNT'].sum()
    
    # cast series to dataframe
    categories_df = categories.to_frame().T
    # reset index accordingly
    categories_df.reset_index(inplace=True, drop=True)    
    
    # add org information into it
    categories_df['Checked_Organisation_Name'] = oscar_segment['Checked_Organisation_Name'][0]
    categories_df['IfG_Organisation_Type'] = oscar_segment['IfG_Organisation_Type'][0]
    categories_df['IfG_Organisation_Status'] = oscar_segment['IfG_Organisation_Status'][0]
    
    return categories_df


def grouping_by_organisation(new_oscar, grouped_new_oscar_df):

    # find the unique list of organisations from OSCAR (again)
    org_long_name_list = new_oscar['ORGANISATION_LONG_NAME'].unique()

    # for each segment/organisation, do something...
    for j in range(0, len(org_long_name_list)):

        # take out the segment from new_oscar
        oscar_segment = new_oscar[new_oscar['ORGANISATION_LONG_NAME']==org_long_name_list[j]]
        # reset its index
        oscar_segment.reset_index(drop=True, inplace=True)

        # take the top code & long name
        org_long_name = org_long_name_list[j]
        org_code = oscar_segment['ORGANISATION_CODE'][0]

        # run a matching routine
        oscar_segment = organisation_matching(org_code, org_long_name, grouped_new_oscar_df, oscar_segment)

        # pull out the values desired
        org_summary_df = summarise_org_spending(org_code, org_long_name, oscar_segment)

        # append the segments again for future reference
        if j == 0:
            all_oscar = oscar_segment
            summary_totals = org_summary_df
        else:
            all_oscar = pd.concat([all_oscar, oscar_segment], ignore_index=True)
            summary_totals = pd.concat([summary_totals, org_summary_df], ignore_index=True)

    return all_oscar, summary_totals

In [3]:
def organisation_code_extraction(new_oscar):
    
    # make a list of unique oscar organisations from the current data release
    new_oscar_orgs = new_oscar['ORGANISATION_LONG_NAME'].unique()
    
    # find the associated code for each organisation
    new_org_codes = []

    for org in new_oscar_orgs:

        # find org in the new_oscar dataset
        org_df = new_oscar[new_oscar['ORGANISATION_LONG_NAME']==org]

        # find unique codes
        org_code = org_df['ORGANISATION_CODE'].unique()

        if len(org_code) > 1:
            print('more than one org code found for '+org+': '+org_code)
            new_org_codes.append(org_code[0])
        else:
            new_org_codes.append(org_code[0])

    # cast results into a dataframe listing only the organisations and codes from the oscar file
    new_oscar_orgs_df = pd.DataFrame(list(zip(new_oscar_orgs, new_org_codes)),
                                     columns=['ORGANISATION_LONG_NAME','ORGANISATION_CODE'])
    
    return new_oscar_orgs_df

In [16]:
def checking_organisations(new_oscar_orgs_df, baseline_oscar, file_name):
    
    # initialise somewhere to store the checking information
    chk_org = []
    typ_org = []
    sts_org = []
    unfound_orgs = []

    # run through the list of organisations in latest dataset and find matched information from the baseline
    for j in range(0, len(new_oscar_orgs_df)):

        try:
            chk_org.append(baseline_oscar[baseline_oscar['ORGANISATION_CODE']==new_oscar_orgs_df['ORGANISATION_CODE'][j]]['Checked_Organisation_Name'].iloc[0])
            typ_org.append(baseline_oscar[baseline_oscar['ORGANISATION_CODE']==new_oscar_orgs_df['ORGANISATION_CODE'][j]]['IfG_Organisation_Type'].iloc[0])
            sts_org.append(baseline_oscar[baseline_oscar['ORGANISATION_CODE']==new_oscar_orgs_df['ORGANISATION_CODE'][j]]['IfG_Organisation_Status'].iloc[0])
        except IndexError:
            print(new_oscar_orgs_df['ORGANISATION_LONG_NAME'][j] + ' not found in ' + file_name)
            chk_org.append('CHECK_NEW')
            typ_org.append('CHECK_NEW')
            sts_org.append('CHECK_NEW')
            unfound_orgs.append(new_oscar_orgs_df['ORGANISATION_LONG_NAME'][j])

    # assemble into one dataframe

    checked_orgs_df = new_oscar_orgs_df
    checked_orgs_df['Checked_Organisation_Name'] = chk_org
    checked_orgs_df['IfG_Organisation_Type'] = typ_org
    checked_orgs_df['IfG_Organisation_Status'] = sts_org  
    
    unfound_orgs_df = pd.DataFrame(unfound_orgs, columns=[file_name])
    
    return checked_orgs_df, unfound_orgs_df
    

In [17]:
def checking_organisations_no_unfound(new_oscar_orgs_df, baseline_oscar, file_name):
    
    # read in unfound checking
    unfound_org_df = pd.read_excel('oscar_organisation_matching_unfound.xlsx')
    
    # initialise somewhere to store the checking information
    chk_org = []
    typ_org = []
    sts_org = []

    # run through the list of organisations in latest dataset and find matched information from the baseline
    for j in range(0, len(new_oscar_orgs_df)):

        try:
            chk_org.append(baseline_oscar[baseline_oscar['ORGANISATION_CODE']==new_oscar_orgs_df['ORGANISATION_CODE'][j]]['Checked_Organisation_Name'].iloc[0])
            typ_org.append(baseline_oscar[baseline_oscar['ORGANISATION_CODE']==new_oscar_orgs_df['ORGANISATION_CODE'][j]]['IfG_Organisation_Type'].iloc[0])
            sts_org.append(baseline_oscar[baseline_oscar['ORGANISATION_CODE']==new_oscar_orgs_df['ORGANISATION_CODE'][j]]['IfG_Organisation_Status'].iloc[0])
        except IndexError:
            chk_org.append(new_oscar_orgs_df['ORGANISATION_LONG_NAME'][j])
            typ_org.append(unfound_org_df[unfound_org_df['ORGANISATION_LONG_NAME']==new_oscar_orgs_df['ORGANISATION_LONG_NAME'][j]]['Type_of_organisation']) #.iloc[0])
            sts_org.append(unfound_org_df[unfound_org_df['ORGANISATION_LONG_NAME']==new_oscar_orgs_df['ORGANISATION_LONG_NAME'][j]]['Exact Status']) #.iloc[0])
            
    # assemble into one dataframe

    checked_orgs_df = new_oscar_orgs_df
    checked_orgs_df['Checked_Organisation_Name'] = chk_org
    checked_orgs_df['IfG_Organisation_Type'] = typ_org
    checked_orgs_df['IfG_Organisation_Status'] = sts_org  
    
    return checked_orgs_df
    

In [18]:
def clean_group_oscar_lite(all_oscar):

    # filter oscar dataframe to be only R13 final outturn numbers
    R13_df = all_oscar[all_oscar['VERSION_CODE']=='R13']

    # ensure only confirmed data is brought through
    annual_data = R13_df[R13_df['STATUS_CODE']=='CONFIRMED']

    # exclude NON-BUDGET, NON-VOTED
#    cleaned_data = annual_data[annual_data['CONTROL_BUDGET_L0_LONG_NAME']!='NON-BUDGET']
#    cleaned_data = cleaned_data[cleaned_data['ACCOUNTING_AUTHORITY_L0_CODE']!='NON-VOTED']
    cleaned_data = annual_data
    # reset index of cleaned data
    cleaned_data.reset_index(drop=True, inplace=True)

    # take each organisation in turn for grouping...
    organisations = cleaned_data['ORGANISATION_LONG_NAME'].unique()
    # for each orgasnisation
    for j in range(0, len(organisations)):
        # reset index (i.e. obtain oscar segment)
        org_data = cleaned_data[cleaned_data['ORGANISATION_LONG_NAME']==organisations[j]].reset_index(drop=True)
        # group the data according to a set of budgetry groups
        org_grouped = org_data.groupby([
            'PESA_ECONOMIC_BUDGET_CODE',
            'PESA_ECONOMIC_GROUP_CODE',
            'CONTROL_BUDGET_L0_LONG_NAME',
            'CONTROL_BUDGET_L1_LONG_NAME',
            'ECONOMIC_CATEGORY_LONG_NAME',
            'ECONOMIC_CATEGORY_CODE',
            'ACCOUNTING_AUTHORITY_L0_CODE',
            'ECONOMIC_GROUP_LONG_NAME',
            'INCOME_CATEGORY_SHORT_NAME',
            'CHART_OF_ACCOUNTS_L5_LONG_NAME',
            'ORGANISATION_TYPE_L1_LONG_NAME'])['AMOUNT'].sum().to_frame()

        # add in general informatino for the organisation
        org_grouped['BUDGETING_ORGANISATIONS_CODE'] = org_data['BUDGETING_ORGANISATIONS_CODE'][0]
        org_grouped['DEPARTMENT_GROUP_CODE'] = org_data['DEPARTMENT_GROUP_CODE'][0]
        org_grouped['DEPARTMENT_GROUP_LONG_NAME'] = org_data['DEPARTMENT_GROUP_LONG_NAME'][0]
        org_grouped['ORGANISATION_CODE'] = org_data['ORGANISATION_CODE'][0]
        org_grouped['ORGANISATION_LONG_NAME'] = org_data['ORGANISATION_LONG_NAME'][0]
        org_grouped['ORGANISATION_TYPE_L1_CODE'] = org_data['ORGANISATION_TYPE_L1_CODE'][0]
        org_grouped['Checked_Organisation_Name'] = org_data['Checked_Organisation_Name'][0]
        org_grouped['IfG_Organisation_Type'] = org_data['IfG_Organisation_Type'][0]
        org_grouped['IfG_Organisation_Status'] = org_data['IfG_Organisation_Status'][0]
        org_grouped['Financial_Year'] = org_data['Financial_Year'][0]

        # assemble the information into a single dataframe
        if j == 0:
            cleaned_group_df = org_grouped
        else:
            cleaned_group_df = pd.concat([cleaned_group_df, org_grouped], ignore_index=False)
            
    # reset index of cleaned up data
    cleaned_group_df.reset_index(inplace=True)
    
    return cleaned_group_df

In [19]:
def clean_group_oscar(all_oscar):

    # filter oscar dataframe to be only R13 final outturn numbers
    R13_df = all_oscar[all_oscar['VERSION_CODE']=='R13']

    # ensure only confirmed data is brought through
    annual_data = R13_df[R13_df['STATUS_CODE']=='CONFIRMED']

    # exclude NON-BUDGET, NON-VOTED
    cleaned_data = annual_data[annual_data['CONTROL_BUDGET_L0_LONG_NAME']!='NON-BUDGET']
    cleaned_data = cleaned_data[cleaned_data['ACCOUNTING_AUTHORITY_L0_CODE']!='NON-VOTED']
    # reset index of cleaned data
    cleaned_data.reset_index(drop=True, inplace=True)

    # take each organisation in turn for grouping...
    organisations = cleaned_data['ORGANISATION_LONG_NAME'].unique()
    # for each orgasnisation
    for j in range(0, len(organisations)):
        # reset index (i.e. obtain oscar segment)
        org_data = cleaned_data[cleaned_data['ORGANISATION_LONG_NAME']==organisations[j]].reset_index(drop=True)
        # group the data according to a set of budgetry groups
        org_grouped = org_data.groupby([
            'PESA_ECONOMIC_BUDGET_CODE',
            'PESA_ECONOMIC_GROUP_CODE',
            'CONTROL_BUDGET_L0_LONG_NAME',
            'CONTROL_BUDGET_L1_LONG_NAME',
            'ECONOMIC_CATEGORY_LONG_NAME',
            'ECONOMIC_CATEGORY_CODE',
            'ACCOUNTING_AUTHORITY_L0_CODE',
            'ECONOMIC_GROUP_LONG_NAME',
            'INCOME_CATEGORY_SHORT_NAME',
            'CHART_OF_ACCOUNTS_L5_LONG_NAME'])['AMOUNT'].sum().to_frame()

        # add in general informatino for the organisation
        org_grouped['BUDGETING_ORGANISATIONS_CODE'] = org_data['BUDGETING_ORGANISATIONS_CODE'][0]
        org_grouped['DEPARTMENT_GROUP_CODE'] = org_data['DEPARTMENT_GROUP_CODE'][0]
        org_grouped['DEPARTMENT_GROUP_LONG_NAME'] = org_data['DEPARTMENT_GROUP_LONG_NAME'][0]
        org_grouped['ORGANISATION_CODE'] = org_data['ORGANISATION_CODE'][0]
        org_grouped['ORGANISATION_LONG_NAME'] = org_data['ORGANISATION_LONG_NAME'][0]
        org_grouped['ORGANISATION_TYPE_L1_CODE'] = org_data['ORGANISATION_TYPE_L1_CODE'][0]
        org_grouped['Checked_Organisation_Name'] = org_data['Checked_Organisation_Name'][0]
        org_grouped['IfG_Organisation_Type'] = org_data['IfG_Organisation_Type'][0]
        org_grouped['IfG_Organisation_Status'] = org_data['IfG_Organisation_Status'][0]
        org_grouped['Financial_Year'] = org_data['Financial_Year'][0]

        # assemble the information into a single dataframe
        if j == 0:
            cleaned_group_df = org_grouped
        else:
            cleaned_group_df = pd.concat([cleaned_group_df, org_grouped], ignore_index=False)
            
    # reset index of cleaned up data
    cleaned_group_df.reset_index(inplace=True)
    
    return cleaned_group_df

In [7]:
baseline_oscar['CONTROL_BUDGET_L1_LONG_NAME'].unique()

array(['DEPARTMENTAL EXPENDITURE LIMITS PROGRAMME',
       'DEPARTMENTAL EXPENDITURE LIMITS ADMINISTRATION',
       'DEPARTMENTAL ANNUALLY MANAGED EXPENDITURE', 'NON-BUDGET (NB)',
       'NON-DEPARTMENTAL ANNUALLY MANAGED EXPENDITURE'], dtype=object)

In [5]:
baseline_oscar.columns

Index(['YEAR_NO', 'YEAR_SHORT_NAME', 'QUARTER_SHORT_NAME', 'MONTH_SHORT_NAME',
       'BUDGETING_ORGANISATIONS_CODE', 'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_CODE',
       'ORGANISATION_TYPE_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE',
       'ORGANISATION_TYPE_L1_LONG_NAME', 'PESA_GROUP_CODE',
       'PESA_GROUP_LONG_NAME', 'SR_GROUP_CODE', 'SR_GROUP_LONG_NAME',
       'BX_VALIDATION_GROUP_CODE', 'BX_VALIDATION_GROUP_LONG_NAME',
       'FO_VALIDATION_GROUP_CODE', 'FO_VALIDATION_GROUP_LONG_NAME',
       'ACCOUNTING_ARRANGEMENTS_CODE', 'ACCOUNTING_ARRANGEMENTS_LONG_NAME',
       'COUNTER_ORGANISATION_CODE', 'COUNTER_ORGANISATION_LONG_NAME',
       'SEGMENT_L4_CODE', 'SEGMENT_L4_LONG_NAME', 'COFOG_L0_CODE',
       'COFOG_L0_LONG_NAME', 'COFOG_L1_CODE', 'COFOG_L1_LONG_NAME',
       'COFOG_L2_CODE', 'COFOG_L2_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME',
       'CONTROL_BUDGET_L1_LONG_NAME', 'COVERAGE_L

In [20]:
all_oscar_df.columns

Index(['YEAR_NO', 'YEAR_SHORT_NAME', 'QUARTER_SHORT_NAME', 'MONTH_SHORT_NAME',
       'BUDGETING_ORGANISATIONS_CODE', 'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_CODE',
       'ORGANISATION_TYPE_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE',
       'ORGANISATION_TYPE_L1_LONG_NAME', 'PESA_GROUP_CODE',
       'PESA_GROUP_LONG_NAME', 'SR_GROUP_CODE', 'SR_GROUP_LONG_NAME',
       'BX_VALIDATION_GROUP_CODE', 'BX_VALIDATION_GROUP_LONG_NAME',
       'FO_VALIDATION_GROUP_CODE', 'FO_VALIDATION_GROUP_LONG_NAME',
       'ACCOUNTING_ARRANGEMENTS_CODE', 'ACCOUNTING_ARRANGEMENTS_LONG_NAME',
       'COUNTER_ORGANISATION_CODE', 'COUNTER_ORGANISATION_LONG_NAME',
       'SEGMENT_L4_CODE', 'SEGMENT_L4_LONG_NAME', 'COFOG_L0_CODE',
       'COFOG_L0_LONG_NAME', 'COFOG_L1_CODE', 'COFOG_L1_LONG_NAME',
       'COFOG_L2_CODE', 'COFOG_L2_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME',
       'CONTROL_BUDGET_L1_LONG_NAME', 'COVERAGE_L

In [88]:
grouped_cleaned_data = cleaned_data.groupby(['BUDGETING_ORGANISATIONS_CODE', 'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_CODE',
       'ORGANISATION_TYPE_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE',
       'ORGANISATION_TYPE_L1_LONG_NAME'])['AMOUNT'].sum()

In [90]:
grouped_cleaned_data.to_frame()

AMOUNT
BUDGETING_ORGANISATIONS_CODE DEPARTMENT_GROUP_CODE DEPARTMENT_GROUP_LONG_NAME                         ORGANISATION_CODE ORGANISATION_LONG_NAME                         ORGANISATION_TYPE_CODE ORGANISATION_TYPE_LONG_NAME ORGANISATION_TYPE_L1_CODE ORGANISATION_TYPE_L1_LONG_NAME            
DEPARTMENTS                  AFS902.GROUP          Armed Forces Pension and Compensation Schemes      AFS902            Armed Forces Pension and Compensation Schemes  CG                     CENTRAL GOVERNMENT          PENSION                   PENSION SCHEME                   6711187.0
                             BIS084.GROUP          Department for Business, Energy and Industrial ... ACA084            Advisory, Conciliation and Arbitration Service CG                     CENTRAL GOVERNMENT          ALB                       ARMS LENGTH BODY                   56147.0
                                                                                                      BBB084            British Business Bank plc                      CG                     CENTRAL GOVERNMENT          ALB                       ARMS LENGTH BODY                  -37741.0
                                                                                                      BIS084            Department for Business Innovation and Skills  CG                     CENTRAL GOVERNMENT          DEPT                      DEPARTMENT                      13812756.0
                                                                                                      BPA084            BIS (Postal Services Act 2011) Company Limited CG                     CENTRAL GOVERNMENT          ALB                       ARMS LENGTH BODY                  -29824.0
...                                                                                                                                                                                                                                                                                        ...
                             UKT013.GROUP          Department for International Trade                 TRA013            Trade Remedies Authority (TRA)                 CG                     CENTRAL GOVERNMENT          ALB                       ARMS LENGTH BODY                   10965.0
                                                                                                      UKT013            Department for International Trade             CG                     CENTRAL GOVERNMENT          DEPT                      DEPARTMENT                        554591.0
                             WOF091.GROUP          Wales Office                                       WOF091            Wales Office                                   CG                     CENTRAL GOVERNMENT          DEPT                      DEPARTMENT                          5609.0
                             WSR057.GROUP          Water Services Regulation Authority                WSR057            Water Services Regulation Authority            CG                     CENTRAL GOVERNMENT          DEPT                      DEPARTMENT                          -415.0
DEVOLVED ADMINISTRATIONS     NIE099.GROUP          Northern Ireland Executive                         NIE099            Northern Ireland Executive                     CG                     CENTRAL GOVERNMENT          DEVOLVED                  DEVOLVED ADMINISTRATION             1222.0

[216 rows x 1 columns]

In [71]:
cleaned_data

YEAR_NO YEAR_SHORT_NAME QUARTER_SHORT_NAME MONTH_SHORT_NAME  \
0          2021         2021-22       Qtr3 - 21-22           Dec-21   
1          2021         2021-22       Qtr1 - 21-22           May-21   
2          2021         2021-22       Qtr2 - 21-22           Jul-21   
3          2021         2021-22       Qtr4 - 21-22           Mar-22   
4          2021         2021-22       Qtr2 - 21-22           Aug-21   
...         ...             ...                ...              ...   
119508     2021         2021-22       Qtr3 - 21-22           Dec-21   
119509     2021         2021-22       Qtr4 - 21-22           Mar-22   
119510     2021         2021-22       Qtr1 - 21-22           Jun-21   
119511     2021         2021-22       Qtr3 - 21-22           Nov-21   
119512     2021         2021-22       Qtr2 - 21-22           Sep-21   

       BUDGETING_ORGANISATIONS_CODE DEPARTMENT_GROUP_CODE  \
0                       DEPARTMENTS          MOD017.GROUP   
1                       DEPARTMENTS          MOD017.GROUP   
2                       DEPARTMENTS          MOD017.GROUP   
3                       DEPARTMENTS          MOD017.GROUP   
4                       DEPARTMENTS          MOD017.GROUP   
...                             ...                   ...   
119508                  DEPARTMENTS          DFT004.GROUP   
119509                  DEPARTMENTS          DFT004.GROUP   
119510                  DEPARTMENTS          DFT004.GROUP   
119511                  DEPARTMENTS          DFT004.GROUP   
119512                  DEPARTMENTS          DFT004.GROUP   

       DEPARTMENT_GROUP_LONG_NAME ORGANISATION_CODE  \
0             Ministry of Defence            MOD017   
1             Ministry of Defence            MOD017   
2             Ministry of Defence            MOD017   
3             Ministry of Defence            MOD017   
4             Ministry of Defence            MOD017   
...                           ...               ...   
119508   Department for Transport            LCR004   
119509   Department for Transport            LCR004   
119510   Department for Transport            LCR004   
119511   Department for Transport            LCR004   
119512   Department for Transport            LCR004   

                 ORGANISATION_LONG_NAME ORGANISATION_TYPE_CODE  ...  \
0                   Ministry of Defence                     CG  ...   
1                   Ministry of Defence                     CG  ...   
2                   Ministry of Defence                     CG  ...   
3                   Ministry of Defence                     CG  ...   
4                   Ministry of Defence                     CG  ...   
...                                 ...                    ...  ...   
119508  London and Continental Railways                     CG  ...   
119509  London and Continental Railways                     CG  ...   
119510  London and Continental Railways                     CG  ...   
119511  London and Continental Railways                     CG  ...   
119512  London and Continental Railways                     CG  ...   

       VERSION_CODE FCT_LOAD_TYPE_CODE       FCT_LOAD_TYPE_LONG_NAME  \
0               R13           EP_APP9_  COGNOS EP Forecast Outturn B   
1               R13           EP_APP9_  COGNOS EP Forecast Outturn B   
2               R13           EP_APP9_  COGNOS EP Forecast Outturn B   
3               R13           EP_APP9_  COGNOS EP Forecast Outturn B   
4               R13           EP_APP9_  COGNOS EP Forecast Outturn B   
...             ...                ...                           ...   
119508          R13           EP_APP9_  COGNOS EP Forecast Outturn B   
119509          R13           EP_APP9_  COGNOS EP Forecast Outturn B   
119510          R13           EP_APP9_  COGNOS EP Forecast Outturn B   
119511          R13           EP_APP9_  COGNOS EP Forecast Outturn B   
119512          R13           EP_APP9_  COGNOS EP Forecast Outturn B   

       ROW_DESCRIPTION  DATA_ID   AMOUNT DA

In [65]:
R13_df['STATUS_CODE'].unique()

array(['CONFIRMED'], dtype=object)

In [60]:
R13_df.columns

Index(['YEAR_NO', 'YEAR_SHORT_NAME', 'QUARTER_SHORT_NAME', 'MONTH_SHORT_NAME',
       'BUDGETING_ORGANISATIONS_CODE', 'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_CODE',
       'ORGANISATION_TYPE_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE',
       'ORGANISATION_TYPE_L1_LONG_NAME', 'PESA_GROUP_CODE',
       'PESA_GROUP_LONG_NAME', 'SR_GROUP_CODE', 'SR_GROUP_LONG_NAME',
       'BX_VALIDATION_GROUP_CODE', 'BX_VALIDATION_GROUP_LONG_NAME',
       'FO_VALIDATION_GROUP_CODE', 'FO_VALIDATION_GROUP_LONG_NAME',
       'ACCOUNTING_ARRANGEMENTS_CODE', 'ACCOUNTING_ARRANGEMENTS_LONG_NAME',
       'COUNTER_ORGANISATION_CODE', 'COUNTER_ORGANISATION_LONG_NAME',
       'SEGMENT_L4_CODE', 'SEGMENT_L4_LONG_NAME', 'COFOG_L0_CODE',
       'COFOG_L0_LONG_NAME', 'COFOG_L1_CODE', 'COFOG_L1_LONG_NAME',
       'COFOG_L2_CODE', 'COFOG_L2_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME',
       'CONTROL_BUDGET_L1_LONG_NAME', 'COVERAGE_L

In [30]:
file_names[0][:-4]

'2015_OSCAR_Extract_2010_11'

In [24]:
all_oscar_df = pd.read_pickle(file_names[0][:-4]+'_matched.pkl')

In [26]:
new_matching_information = pd.read_excel('Change in Status from WM23 folder.xlsx')

In [32]:
# build up a focused list for checking...
oscar_unique_orgs = all_oscar_df['ORGANISATION_LONG_NAME'].unique()

In [65]:
# flesh this out with critical information
for j in range(0, len(oscar_unique_orgs)):
    # match the unique organisation
    oscar_unique_mini = all_oscar_df[all_oscar_df['ORGANISATION_LONG_NAME']==oscar_unique_orgs[j]]
    # take the first row
    oscar_unique_mini = oscar_unique_mini.iloc[0][['YEAR_NO','ORGANISATION_LONG_NAME', 'ORGANISATION_CODE', 'Checked_Organisation_Name',
       'IfG_Organisation_Type', 'IfG_Organisation_Status', 'Financial_Year']]
    # put series as a dataframe
    oscar_mini_df = oscar_unique_mini.to_frame().T
    if j == 0:
        oscar_mini_all_df = oscar_mini_df
    else:
        oscar_mini_all_df = pd.concat([oscar_mini_all_df, oscar_mini_df])

In [66]:
oscar_mini_all_df

YEAR_NO                             ORGANISATION_LONG_NAME  \
0        2010                          The Planning Inspectorate   
26       2010                         Department of Health (NHS)   
459      2010         Teachers' Pension Scheme (England & Wales)   
511      2010                                Ministry of Justice   
796      2010                              Student Loans Company   
...       ...                                                ...   
17156    2010                                        NHS Estates   
17157    2010  Medicines and Healthcare Products Regulatory A...   
17158    2010               Vehicle and Operator Services Agency   
17159    2010               Commonwealth Development Corporation   
17160    2010                                 London Underground   

      ORGANISATION_CODE                          Checked_Organisation_Name  \
0                IPC085                          The Planning Inspectorate   
26               DOH033                         Department of Health (NHS)   
459              TPS904  CHECK: Teachers' Pension Scheme (England & Wales)   
511              MOJ047                                Ministry of Justice   
796              SLC084                                          CHECK_NEW   
...                 ...                                                ...   
17156            NET033                                          CHECK_NEW   
17157            MHP033                                          CHECK_NEW   
17158            VOS004                                          CHECK_NEW   
17159            CDC030                                          CHECK_NEW   
17160            ELU101                          CHECK: London Underground   

      IfG_Organisation_Type IfG_Organisation_Status Financial_Year  
0               Public Body        Executive Agency        2010_11  
26               Department              Department        2010_11  
459              Department              Department        2010_11  
511              Department              Department        2010_11  
796               CHECK_NEW               CHECK_NEW        2010_11  
...                     ...                     ...            ...  
17156             CHECK_NEW               CHECK_NEW        2010_11  
17157             CHECK_NEW               CHECK_NEW        2010_11  
17158             CHECK_NEW               CHECK_NEW        2010_11  
17159             CHECK_NEW               CHECK_NEW        2010_11  
17160              Devolved                Devolved        2010_11  

[261 rows x 7 columns]

In [61]:
oscar_mini_all_df

YEAR_NO     ORGANISATION_LONG_NAME ORGANISATION_CODE  \
0    2010  The Planning Inspectorate            IPC085   
0    2010  The Planning Inspectorate            IPC085   

   Checked_Organisation_Name IfG_Organisation_Type IfG_Organisation_Status  \
0  The Planning Inspectorate           Public Body        Executive Agency   
0  The Planning Inspectorate           Public Body        Executive Agency   

  Financial_Year  
0        2010_11  
0        2010_11

In [44]:
type(oscar_unique_mini)

pandas.core.series.Series

In [27]:
new_matching_information

Organisation  \
0                                The National Archives   
1                      Government Actuary's Department   
2                                   Charity Commission   
3                     National Savings and Investments   
4                                Food Standards Agency   
..                                                 ...   
293                   Capacity Market Settlements Body   
294                                    Post Office Ltd   
295                                  Royal Navy Museum   
296  Disabled People's Employment Corporation (GB) Ltd   
297                               Royal Marines Museum   

    Organisation Type Pre-2010      Exact Status pre-2010  \
0                          Same                       NaN   
1                          Same                       NaN   
2                          Same                       NaN   
3                          Same                       NaN   
4                          Same                       NaN   
..                          ...                       ...   
293                 Public Body  Government owned company   
294                        Same                       NaN   
295                        Same                       NaN   
296                 Public Body            Executive NDPB   
297                        Same                       NaN   

          Date of Change Organisation Type After        Exact Status After  \
0                    NaN                     NaN                       NaN   
1                    NaN                     NaN                       NaN   
2                    NaN                     NaN                       NaN   
3                    NaN                     NaN                       NaN   
4                    NaN                     NaN                       NaN   
..                   ...                     ...                       ...   
293  2015-03-31 00:00:00             Public Body  Government owned company   
294                  NaN                     NaN                       NaN   
295                  NaN                     NaN                       NaN   
296  2017-03-31 00:00:00                Bankrupt                  Bankrupt   
297                  NaN                     NaN                       NaN   

                                              Notes  \
0                                               NaN   
1                                               NaN   
2                                               NaN   
3                                               NaN   
4                                               NaN   
..                                              ...   
293  Now called the Electricity Settlements Company   
294                                             NaN   
295                                             NaN   
296                                             NaN   
297                                             NaN   

                                        Current Status  Unnamed: 8 Unnamed: 9  \
0                           Non-ministerial department         NaN        NaN   
1                           Non-ministerial department         NaN        NaN   
2                           Non-ministerial department         NaN        NaN   
3    Non-ministerial department and an executive ag...         NaN        NaN   
4                           Non-ministerial department         NaN        NaN   
..                                                 ...         ...        ...   
293                 Government owned company (renamed)         NaN        NaN   
294                           Government owned company         NaN        NaN   
295                                   NDPB (Executive)         NaN        NaN   
296                                          Abolished         NaN        NaN   
297                                            Charity         NaN        NaN   

    Unnamed: 10  
0           NaN  
1    

In [31]:
all_oscar_df.columns

Index(['YEAR_NO', 'YEAR_SHORT_NAME', 'QUARTER_SHORT_NAME', 'MONTH_SHORT_NAME',
       'BUDGETING_ORGANISATIONS_CODE', 'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_CODE',
       'ORGANISATION_TYPE_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE',
       'ORGANISATION_TYPE_L1_LONG_NAME', 'PESA_GROUP_CODE',
       'PESA_GROUP_LONG_NAME', 'SR_GROUP_CODE', 'SR_GROUP_LONG_NAME',
       'BX_VALIDATION_GROUP_CODE', 'BX_VALIDATION_GROUP_LONG_NAME',
       'FO_VALIDATION_GROUP_CODE', 'FO_VALIDATION_GROUP_LONG_NAME',
       'ACCOUNTING_ARRANGEMENTS_CODE', 'ACCOUNTING_ARRANGEMENTS_LONG_NAME',
       'COUNTER_ORGANISATION_CODE', 'COUNTER_ORGANISATION_LONG_NAME',
       'SEGMENT_L4_CODE', 'SEGMENT_L4_LONG_NAME', 'COFOG_L0_CODE',
       'COFOG_L0_LONG_NAME', 'COFOG_L1_CODE', 'COFOG_L1_LONG_NAME',
       'COFOG_L2_CODE', 'COFOG_L2_LONG_NAME', 'CONTROL_BUDGET_L0_LONG_NAME',
       'CONTROL_BUDGET_L1_LONG_NAME', 'COVERAGE_L

In [7]:
for j in range(0, len(file_names)):
    
    file_location = 'Source files\\' + file_names[j]

    # read the pickle file...
    all_oscar_df = pd.read_pickle(file_names[j][:-4]+'_matched.pkl')

    # clean and group the oscar data
    cleaned_grouped_df = clean_group_oscar_lite(all_oscar_df)
    
    if j == 0:
        data_df = cleaned_grouped_df
    else:
        data_df = pd.concat([data_df, cleaned_grouped_df], ignore_index=True)

In [16]:
temp = data_df[data_df['ORGANISATION_LONG_NAME']=='UK Trade & Investment'].groupby([
            'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE','ORGANISATION_TYPE_L1_LONG_NAME', 'Financial_Year'])['AMOUNT'].sum().to_frame()

In [17]:
temp

AMOUNT
DEPARTMENT_GROUP_CODE DEPARTMENT_GROUP_LONG_NAME ORGANISATION_CODE ORGANISATION_LONG_NAME ORGANISATION_TYPE_L1_CODE ORGANISATION_TYPE_L1_LONG_NAME Financial_Year          
UKT013.GROUP          Uk Trade & Investment      UKT013            UK Trade & Investment  DEPT                      DEPARTMENT                     2010_11          86172.0
                                                                                                                                                   2011_12          84394.0
                                                                                                                                                   2012_13          94106.0
                                                                                                                                                   2013_14         159710.0
                                                                                                                                                   2014_15         265766.0

In [11]:
data_df.columns

Index(['PESA_ECONOMIC_BUDGET_CODE', 'PESA_ECONOMIC_GROUP_CODE',
       'CONTROL_BUDGET_L0_LONG_NAME', 'CONTROL_BUDGET_L1_LONG_NAME',
       'ECONOMIC_CATEGORY_LONG_NAME', 'ECONOMIC_CATEGORY_CODE',
       'ACCOUNTING_AUTHORITY_L0_CODE', 'ECONOMIC_GROUP_LONG_NAME',
       'INCOME_CATEGORY_SHORT_NAME', 'CHART_OF_ACCOUNTS_L5_LONG_NAME',
       'ORGANISATION_TYPE_L1_LONG_NAME', 'AMOUNT',
       'BUDGETING_ORGANISATIONS_CODE', 'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE',
       'Checked_Organisation_Name', 'IfG_Organisation_Type',
       'IfG_Organisation_Status', 'Financial_Year'],
      dtype='object')

In [18]:
temp = data_df[data_df['ORGANISATION_LONG_NAME']=='Independent Living Fund'].groupby([
            'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE','ORGANISATION_TYPE_L1_LONG_NAME', 'Financial_Year'])['AMOUNT'].sum().to_frame()

In [19]:
temp

AMOUNT
DEPARTMENT_GROUP_CODE DEPARTMENT_GROUP_LONG_NAME       ORGANISATION_CODE ORGANISATION_LONG_NAME  ORGANISATION_TYPE_L1_CODE ORGANISATION_TYPE_L1_LONG_NAME Financial_Year          
DWP032.GROUP          Department for Work and Pensions ILF032            Independent Living Fund ALB                       ARMS LENGTH BODY               2010_11         347587.0
                                                                                                                                                          2011_12         333985.0
                                                                                                                                                          2012_13         311164.0
                                                                                                                                                          2013_14         293086.0
                                                                                                                                                          2014_15         281595.0
                                                                                                                                                          2015-16          66147.0

In [22]:
temp = data_df[data_df['ORGANISATION_LONG_NAME']=='Central Office of Information'].groupby([
            'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE','ORGANISATION_TYPE_L1_LONG_NAME', 'Financial_Year'])['AMOUNT'].sum().to_frame()

In [23]:
temp

AMOUNT
DEPARTMENT_GROUP_CODE DEPARTMENT_GROUP_LONG_NAME    ORGANISATION_CODE ORGANISATION_LONG_NAME        ORGANISATION_TYPE_L1_CODE ORGANISATION_TYPE_L1_LONG_NAME Financial_Year        
COI051.GROUP          Central Office of Information COI051            Central Office of Information DEPT                      DEPARTMENT                     2010_11         -656.0
                                                                                                                                                             2012_13            0.0
                                                                                                                                                             2015-16            0.0

In [9]:
data_df['ORGANISATION_LONG_NAME'].unique()

array(['The Planning Inspectorate', 'Department of Health (NHS)',
       "Teachers' Pension Scheme (England & Wales)",
       'Ministry of Justice', 'Student Loans Company', 'CLG Communities',
       'Welsh Assembly Government', 'Legal Aid Fund: Civil',
       'Legal Services Commission',
       'Criminal Injuries Compensation Authority',
       'British Educational Communications and Technology Agency',
       'Department for Business Innovation and Skills',
       'Department of Energy and Climate Change',
       'Children and Family Court Advisory and Support Service',
       'Care Quality Commission', 'General Social Care Council',
       'Foundation Trusts',
       'Qualifications and Curriculum Development Agency',
       'Department for Education', 'Northern Ireland Executive',
       'Bristish Broadcasting Corporation',
       'The Crown Prosecution Service', "Children's Commissioner",
       'Equality and Human Rights Commission',
       'Serious Organised Crime Agency', 'NHS 

In [34]:
temp = data_df[data_df['ORGANISATION_LONG_NAME']=='BPDTS Ltd'].groupby([
            'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE','ORGANISATION_TYPE_L1_LONG_NAME', 'Financial_Year'])['AMOUNT'].sum().to_frame()

In [35]:
temp

AMOUNT
DEPARTMENT_GROUP_CODE DEPARTMENT_GROUP_LONG_NAME       ORGANISATION_CODE ORGANISATION_LONG_NAME ORGANISATION_TYPE_L1_CODE ORGANISATION_TYPE_L1_LONG_NAME Financial_Year         
DWP032.GROUP          Department for Work and Pensions BTS032            BPDTS Ltd              ALB                       ARMS LENGTH BODY               2016-17          3191.0
                                                                                                                                                         2017_18            13.0
                                                                                                                                                         2018_19        -12579.0
                                                                                                                                                         2019_20            -1.0
                                                                                                                                                         2020_21            50.0
                                                                                                                                                         2021_22             0.0

In [32]:
temp = data_df[data_df['ORGANISATION_LONG_NAME']=='Technology Strategy Board'].groupby([
            'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE','ORGANISATION_TYPE_L1_LONG_NAME', 'Financial_Year'])['AMOUNT'].sum().to_frame()

In [33]:
temp

AMOUNT
DEPARTMENT_GROUP_CODE DEPARTMENT_GROUP_LONG_NAME                    ORGANISATION_CODE ORGANISATION_LONG_NAME    ORGANISATION_TYPE_L1_CODE ORGANISATION_TYPE_L1_LONG_NAME Financial_Year          
BIS084.GROUP          Department for Business Innovation and Skills TST084            Technology Strategy Board ALB                       ARMS LENGTH BODY               2010_11         390540.0
                                                                                                                                                                         2011_12         300780.0
                                                                                                                                                                         2012_13         407042.0
                                                                                                                                                                         2013_14         573498.0
                                                                                                                                                                         2014_15         603663.0
                                                                                                                                                                         2015-16         734502.0
                                                                                                                                                                         2016-17         804631.0

In [6]:
file_names[0]

'2015_OSCAR_Extract_2010_11.txt'

In [5]:
all_oscar_df = pd.read_pickle(file_names[0][:-4]+'_matched.pkl')

In [11]:
all_oscar_df[all_oscar_df['ORGANISATION_LONG_NAME']=='Channel Four Television Corporation']

YEAR_NO YEAR_SHORT_NAME QUARTER_SHORT_NAME  MONTH_SHORT_NAME  \
17152     2010         2010-11   Period 0 - 10-11  Period 0 - 10-11   

      BUDGETING_ORGANISATIONS_CODE DEPARTMENT_GROUP_CODE  \
17152                  DEPARTMENTS          DCM048.GROUP   

                    DEPARTMENT_GROUP_LONG_NAME ORGANISATION_CODE  \
17152  Department for Culture, Media and Sport            CFT048   

                    ORGANISATION_LONG_NAME ORGANISATION_TYPE_CODE  ...  \
17152  Channel Four Television Corporation                     PC  ...   

      FCT_LOAD_TYPE_CODE            FCT_LOAD_TYPE_LONG_NAME ROW_DESCRIPTION  \
17152          EP_APP10_  COGNOS EP Publication Adjustments                   

      DATA_ID  AMOUNT DATA_EFFECTIVE_DATETIME Checked_Organisation_Name  \
17152  253600  5800.0     2013-06-21 14:03:22                 CHECK_NEW   

      IfG_Organisation_Type IfG_Organisation_Status Financial_Year  
17152             CHECK_NEW               CHECK_NEW        2010_11  

[1 rows x 95 columns]

In [12]:
all_oscar_df = pd.read_pickle(file_names[10][:-4]+'_matched.pkl')

In [15]:
all_oscar_df['Financial_Year']

0          2020_21
1          2020_21
2          2020_21
3          2020_21
4          2020_21
            ...   
1851351    2020_21
1851352    2020_21
1851353    2020_21
1851354    2020_21
1851355    2020_21
Name: Financial_Year, Length: 1851356, dtype: object

In [5]:
new_classifications = pd.read_excel('oscar_organisation_matching_unfound.xlsx')


In [12]:

for j in range(0, len(file_names)):
    
    all_oscar_df = pd.read_pickle(file_names[j][:-4]+'_matched.pkl')
    
    orgs_for_checking = all_oscar_df['ORGANISATION_LONG_NAME'].unique()

    for k in range(0, len(orgs_for_checking)):

        org_name = orgs_for_checking[k]

        # check for this in the new classifications
        new_info = new_classifications[new_classifications['ORGANISATION_LONG_NAME']==org_name]

        if len(new_info) == 0:
            # do nothing and keep original information
            oscar_df = all_oscar_df[all_oscar_df['ORGANISATION_LONG_NAME']==org_name].reset_index(drop=True)

        else:
            new_info.reset_index(inplace=True, drop=True)

            oscar_df = all_oscar_df[all_oscar_df['ORGANISATION_LONG_NAME']==org_name].reset_index(drop=True)
            oscar_df['IfG_Organisation_Type'] = new_info['Type_of_organisation'][0]
            oscar_df['IfG_Organisation_Status'] = new_info['Exact Status'][0]

        if k == 0:
            extra_checked_oscar_df = oscar_df
        else:
            extra_checked_oscar_df = pd.concat([extra_checked_oscar_df, oscar_df], ignore_index=True)
            
    # write information to pickle
    extra_checked_oscar_df.to_pickle(file_names[j][:-4]+'_extra_checked.pkl')
    
    # condense this into group to avoid massive dataframe...
    extra_checked_oscar_df = clean_group_oscar(extra_checked_oscar_df)
    
    if j == 0:
        all_extra_checked = extra_checked_oscar_df
    else:
        all_extra_checked = pd.concat([all_extra_checked, extra_checked_oscar_df], ignore_index=True)
        
    print(j)
        
all_extra_checked.to_excel('extra_checked_oscar_2023.xlsx')



0
1
2
3
4
5
6
7
8
9
10
11


In [15]:
all_extra_checked['Financial_Year'].unique()

array(['2010_11', '2011_12', '2012_13', '2013_14', '2014_15', '2015-16',
       '2016-17', '2017_18', '2018_19', '2019_20', '2020_21', '2021_22'],
      dtype=object)

In [13]:
extra_cleaned_grouped = clean_group_oscar(all_extra_checked)

extra_cleaned_grouped.to_excel('extra_checked_grouped_oscar_2023.xlsx')

KeyError: 'VERSION_CODE'

In [25]:
all_extra_checked[all_extra_checked['IfG_Organisation_Status']=='CHECK_NEW']['ORGANISATION_LONG_NAME'].unique()

array(['Department of Energy and Climate Change',
       'Independent Living Fund', 'Sustainable Development Commission',
       'UK Infrastructure Bank', 'Pool Reinsurance Company Limited',
       'Trade Remedies Authority (TRA)',
       'Office for Environmental Protection'], dtype=object)

In [16]:
all_extra_checked.columns

Index(['PESA_ECONOMIC_BUDGET_CODE', 'PESA_ECONOMIC_GROUP_CODE',
       'CONTROL_BUDGET_L0_LONG_NAME', 'CONTROL_BUDGET_L1_LONG_NAME',
       'ECONOMIC_CATEGORY_LONG_NAME', 'ECONOMIC_CATEGORY_CODE',
       'ACCOUNTING_AUTHORITY_L0_CODE', 'ECONOMIC_GROUP_LONG_NAME',
       'INCOME_CATEGORY_SHORT_NAME', 'CHART_OF_ACCOUNTS_L5_LONG_NAME',
       'AMOUNT', 'BUDGETING_ORGANISATIONS_CODE', 'DEPARTMENT_GROUP_CODE',
       'DEPARTMENT_GROUP_LONG_NAME', 'ORGANISATION_CODE',
       'ORGANISATION_LONG_NAME', 'ORGANISATION_TYPE_L1_CODE',
       'Checked_Organisation_Name', 'IfG_Organisation_Type',
       'IfG_Organisation_Status', 'Financial_Year'],
      dtype='object')

In [26]:
# quick run through final characterisations...
checked = all_extra_checked[all_extra_checked['IfG_Organisation_Status']!='CHECK_NEW']
checked = checked[checked['IfG_Organisation_Status']!='CHECK']

In [27]:
checked.reset_index(inplace=True, drop=True)

In [28]:
remaining = pd.read_excel('quick_last_check.xlsx')

In [33]:
for j in range(0, len(remaining)):
    
    next_line = all_extra_checked[all_extra_checked['ORGANISATION_LONG_NAME']==remaining['ORGANISATION_LONG_NAME'][j]].reset_index(drop=True)
    
    next_line['IfG_Organisation_Type'] = remaining['IfG_Organisation_Type'][j]
    next_line['IfG_Organisation_Status'] = remaining['IfG_Organisation_Status'][j]
    
    checked = pd.concat([checked, next_line], ignore_index=True)

In [37]:
checked.to_excel('extra_checked_oscar_2023_2.xlsx')

In [29]:
remaining

ORGANISATION_LONG_NAME IfG_Organisation_Type  \
0          House of Commons: Administration  Houses of Parliament   
1                 House of Commons: Members  Houses of Parliament   
2                   Royal Hospital, Chelsea               Charity   
3                            House of Lords  Houses of Parliament   
4      Disclosure and Barring Service (DBS)           Public Body   
5               Churches Conservation Trust               Charity   
6             Nursing and Midwifery Council               Charity   
7                 Fleetbank Funding Limited           Public Body   
8       Parliament: Restoration and Renewal  Houses of Parliament   
9                               Train Fleet           Public Body   
10  Department of Energy and Climate Change            Department   
11                  Independent Living Fund           Public Body   
12       Sustainable Development Commission           Public Body   
13                   UK Infrastructure Bank           Public Body   
14         Pool Reinsurance Company Limited           Public Body   
15           Trade Remedies Authority (TRA)           Public Body   
16      Office for Environmental Protection           Public Body   

   IfG_Organisation_Status  
0     Houses of Parliament  
1     Houses of Parliament  
2                  Charity  
3     Houses of Parliament  
4                     NDPB  
5                  Charity  
6                  Charity  
7       Public corporation  
8     Houses of Parliament  
9        Other public body  
10              Department  
11                    NDPB  
12                    NDPB  
13      Public corporation  
14      Public corporation  
15                    NDPB  
16                    NDPB